In [1]:
import os
import matplotlib.pyplot as plt
import numpy as np
import scipy.stats as stats
import pandas as pd
import altair
import seaborn
RANDOM_SEED = 511
rng = np.random.default_rng(RANDOM_SEED)
seaborn.set_theme(style="darkgrid")
altair.renderers.enable('mimetype')
db_url = os.getenv('DB_URL')
%load_ext autoreload
%autoreload 2
import sys
sys.path.append('../')
from lib import adjust_pairplot_axes

In [13]:
import geopandas
import geoplot

In [63]:
## Felony arrests by census tract (larger than block)

sql = """
SELECT
    boroct2020,
    cdta_name,
    borough_district_code,
    bounding_geography AS shape,
    ct_arrests,
    districts.district_name
FROM census_tracts
    JOIN districts USING (borough_district_code)
    LEFT JOIN (
        SELECT boroct2020, count(*) AS ct_arrests
        FROM arrests
        GROUP BY 1
    ) AS a USING (boroct2020)
"""

sql2 = """
SELECT
    bctcb2020,
    cdta_name,
    borough_district_code,
    bounding_geography AS shape,
    coalesce(ct_arrests, 0) as ct_arrests,
    districts.district_name
FROM census_blocks
    JOIN districts USING (borough_district_code)
    LEFT JOIN (
        SELECT bctcb2020, count(*) AS ct_arrests
        FROM arrests
        GROUP BY 1
    ) AS a USING (bctcb2020)
"""

df = geopandas.GeoDataFrame.from_postgis(sql, db_url, geom_col='shape', index_col='boroct2020')
# df = geopandas.GeoDataFrame.from_postgis(sql2, db_url, geom_col='shape', index_col='bctcb2020')

print(df.shape)
df.head(3).T

(2305, 5)


boroct2020                                                       1000100  \
cdta_name              MN01 Financial District-Tribeca (CD 1 Equivalent)   
borough_district_code                                                101   
shape                  MULTIPOLYGON Z (((-74.04387746892274 40.690187...   
ct_arrests                                                           NaN   
district_name                                               Tribeca/FIDI   

boroct2020                                                       1000201  \
cdta_name               MN03 Lower East Side-Chinatown (CD 3 Equivalent)   
borough_district_code                                                103   
shape                  MULTIPOLYGON Z (((-73.98642897167305 40.705068...   
ct_arrests                                                         245.0   
district_name                                            Lower East Side   

boroct2020                                                       1000600  
cdta_name               MN03 Lower East Side-Chinatown (CD 3 Equivalent)  
borough_district_code                                                103  
shape                  MULTIPOLYGON Z (((-73.99021995337452 40.714404...  
ct_arrests                                                         638.0  
district_name                                            Lower East Side

In [64]:
df.explore(
    column='ct_arrests',
    legend=True,
    color='white',
    style_kwds={'stroke': False}
)

In [62]:
df.ct_arrests.sum()

40057.0